In [2]:
import arcpy
import os
import glob
import numpy as np
import pandas as pd
import sys

In [3]:
in_excel = "warnings_balkan copy.xlsx"

In [40]:
fgdb = arcpy.CreateFileGDB_management(out_folder_path=os.getcwd(), out_name="Workspace9.gdb").getOutput(0)

In [41]:
fgdb_table = arcpy.ExcelToTable_conversion(in_excel, os.path.join(fgdb, "warnings_balkan")).getOutput(0)

In [42]:
input_schema_dict = {}
for field in arcpy.ListFields(fgdb_table):
    input_schema_dict[field.name] = field.type

In [43]:
# input_fields = [field.name for field in arcpy.ListFields(fgdb_table)]
input_fields = list(input_schema_dict.keys())

In [44]:
poly_fc = arcpy.CreateFeatureclass_management(out_path=fgdb, out_name="warnings_balkan_poly", geometry_type="POLYGON", spatial_reference="4326").getOutput(0)

In [45]:
# Add needed attribute fields to the target poly FC
for field in input_schema_dict:
    if field == "OBJECTID":
        pass
    elif field == "WaText":
        print("Adding field {0}...".format(field))
        # Add field with data type from schema dict
        arcpy.AddField_management(poly_fc, str(field), input_schema_dict[field], field_length=5000)
    else:
        print("Adding field {0}...".format(field))
        # Add field with data type from schema dict
        arcpy.AddField_management(poly_fc, str(field), input_schema_dict[field])

Adding field WaId...
Adding field CountryCaption...
Adding field AreaCaption...
Adding field EMMA_ID...
Adding field Polygon...
Adding field WaLevel...
Adding field AWTCaption...
Adding field WaType...
Adding field WaFrom...
Adding field WaTo...
Adding field WaText...


In [46]:
# Helper function to create polygon object for an insert cursor
def prepare_polygon_object(poly_coords, return_objects_list=False):
    single_feature_geometry = []
    for coord_pair in poly_coords.split(" "):
        if coord_pair == '':
            pass
        else:
            # Change string to floats
            float_coord_pair = [float(coord) for coord in coord_pair.split(",")]
            single_feature_geometry.append(float_coord_pair)
    all_features_geometry = [single_feature_geometry]
    
    polygon_objects_list = []

    for feature in all_features_geometry:
        # Create a point object
        list_of_points = []
        for coordinate_pair in feature:
            y_vertex = coordinate_pair[0]
            x_vertex = coordinate_pair[1]
            point_object = arcpy.Point(x_vertex, y_vertex)
            list_of_points.append(point_object)

        # Create an arcpy array
        ap_array = arcpy.Array(list_of_points)
        # Create a polygon object
        polygon_obj = arcpy.Polygon(ap_array)
        # Append to the objects list
        polygon_objects_list.append(polygon_obj)
    if return_objects_list:
        return polygon_objects_list
    else:
        return polygon_obj

In [47]:
insertcursor_field_list = ["SHAPE@"] + list(input_schema_dict.keys())

In [49]:
# Start iterating on the target Polygonal FC with an insert cursor
with arcpy.da.InsertCursor(poly_fc, insertcursor_field_list) as insertcursor:
    
    # Start iterating on the input file geodatabase table with a searchcursor
    with arcpy.da.SearchCursor(fgdb_table, input_fields) as searchcursor:
        for row in searchcursor:
            objectid = row[0]
            waid = row[1]
            country_caption = row[2]
            area_caption = row[3]
            emma_id = row[4]
            polygon = row[5]
            walevel = row[6]
            awtcaption = row[7]
            watype = row[8]
            wafrom = row[9]
            wato = row[10]
            watext = row[11]
            print("Processing row with Object ID of {0}".format(str(objectid)))
            
            try:
                polygon_objects_list = prepare_polygon_object(polygon)
                insert_vals = (polygon_objects_list, 
                               objectid,
                               waid,
                               country_caption,
                               area_caption,
                               emma_id,
                               "NA",
                               walevel,
                               awtcaption,
                               watype,
                               wafrom,
                               wato,
                               watext)
                insertcursor.insertRow(insert_vals)
            
            except RuntimeError:
                print("An attribute could not be written!")
                print(str(RuntimeError))
                print("Attempting to write without text attribute.")
                polygon_objects_list = prepare_polygon_object(polygon)
                insert_vals = (polygon_objects_list, 
                               objectid,
                               waid,
                               country_caption,
                               area_caption,
                               emma_id,
                               "NA",
                               walevel,
                               awtcaption,
                               watype,
                               wafrom,
                               wato,
                               "Unable to write Text")
                insertcursor.insertRow(insert_vals)
            
            except ValueError:
                print("Could not read geometry from input list. Bypassing...")

Processing row with Object ID of 1
Processing row with Object ID of 2
Processing row with Object ID of 3
Processing row with Object ID of 4
Processing row with Object ID of 5
Processing row with Object ID of 6
Processing row with Object ID of 7
Processing row with Object ID of 8
Processing row with Object ID of 9
Processing row with Object ID of 10
Processing row with Object ID of 11
Processing row with Object ID of 12
Processing row with Object ID of 13
Processing row with Object ID of 14
Processing row with Object ID of 15
Processing row with Object ID of 16
Processing row with Object ID of 17
Processing row with Object ID of 18
Processing row with Object ID of 19
Processing row with Object ID of 20
Processing row with Object ID of 21
Processing row with Object ID of 22
Processing row with Object ID of 23
Processing row with Object ID of 24
Processing row with Object ID of 25
Processing row with Object ID of 26
Processing row with Object ID of 27
Processing row with Object ID of 28
P

Processing row with Object ID of 430
Processing row with Object ID of 431
Processing row with Object ID of 432
Processing row with Object ID of 433
Processing row with Object ID of 434
Processing row with Object ID of 435
Processing row with Object ID of 436
Processing row with Object ID of 437
Processing row with Object ID of 438
Processing row with Object ID of 439
Processing row with Object ID of 440
Processing row with Object ID of 441
Processing row with Object ID of 442
Processing row with Object ID of 443
Processing row with Object ID of 444
Processing row with Object ID of 445
Processing row with Object ID of 446
Processing row with Object ID of 447
Processing row with Object ID of 448
Processing row with Object ID of 449
Processing row with Object ID of 450
Processing row with Object ID of 451
Processing row with Object ID of 452
Processing row with Object ID of 453
Processing row with Object ID of 454
Processing row with Object ID of 455
Processing row with Object ID of 456
P

Processing row with Object ID of 1225
Processing row with Object ID of 1226
Processing row with Object ID of 1227
Processing row with Object ID of 1228
Processing row with Object ID of 1229
Processing row with Object ID of 1230
Processing row with Object ID of 1231
Processing row with Object ID of 1232
Processing row with Object ID of 1233
Processing row with Object ID of 1234
Processing row with Object ID of 1235
Processing row with Object ID of 1236
Processing row with Object ID of 1237
Processing row with Object ID of 1238
Processing row with Object ID of 1239
Processing row with Object ID of 1240
Processing row with Object ID of 1241
Processing row with Object ID of 1242
Processing row with Object ID of 1243
Processing row with Object ID of 1244
Processing row with Object ID of 1245
Processing row with Object ID of 1246
Processing row with Object ID of 1247
Processing row with Object ID of 1248
Processing row with Object ID of 1249
Processing row with Object ID of 1250
Processing r

Processing row with Object ID of 1763
Processing row with Object ID of 1764
Processing row with Object ID of 1765
Processing row with Object ID of 1766
Processing row with Object ID of 1767
Processing row with Object ID of 1768
Processing row with Object ID of 1769
Processing row with Object ID of 1770
Processing row with Object ID of 1771
Processing row with Object ID of 1772
Processing row with Object ID of 1773
Processing row with Object ID of 1774
Processing row with Object ID of 1775
Processing row with Object ID of 1776
Processing row with Object ID of 1777
Processing row with Object ID of 1778
Processing row with Object ID of 1779
Processing row with Object ID of 1780
Processing row with Object ID of 1781
Processing row with Object ID of 1782
Processing row with Object ID of 1783
Processing row with Object ID of 1784
Processing row with Object ID of 1785
Processing row with Object ID of 1786
Processing row with Object ID of 1787
Processing row with Object ID of 1788
Processing r

Processing row with Object ID of 2362
Processing row with Object ID of 2363
Processing row with Object ID of 2364
Processing row with Object ID of 2365
Processing row with Object ID of 2366
Processing row with Object ID of 2367
Processing row with Object ID of 2368
Processing row with Object ID of 2369
Processing row with Object ID of 2370
Processing row with Object ID of 2371
Processing row with Object ID of 2372
Processing row with Object ID of 2373
Processing row with Object ID of 2374
Processing row with Object ID of 2375
Processing row with Object ID of 2376
Processing row with Object ID of 2377
Processing row with Object ID of 2378
Processing row with Object ID of 2379
Processing row with Object ID of 2380
Processing row with Object ID of 2381
Processing row with Object ID of 2382
Processing row with Object ID of 2383
Processing row with Object ID of 2384
Processing row with Object ID of 2385
Processing row with Object ID of 2386
Processing row with Object ID of 2387
Processing r

...

Processing row with Object ID of 106690
Processing row with Object ID of 106691
Processing row with Object ID of 106692
Processing row with Object ID of 106693
Processing row with Object ID of 106694
Processing row with Object ID of 106695
Processing row with Object ID of 106696
Processing row with Object ID of 106697
Processing row with Object ID of 106698
Processing row with Object ID of 106699
Processing row with Object ID of 106700
Processing row with Object ID of 106701
Processing row with Object ID of 106702
Processing row with Object ID of 106703
Processing row with Object ID of 106704
Processing row with Object ID of 106705
Processing row with Object ID of 106706
Processing row with Object ID of 106707
Processing row with Object ID of 106708
Processing row with Object ID of 106709
Processing row with Object ID of 106710
Processing row with Object ID of 106711
Processing row with Object ID of 106712
Processing row with Object ID of 106713
Processing row with Object ID of 106714


Processing row with Object ID of 107295
Processing row with Object ID of 107296
Processing row with Object ID of 107297
Processing row with Object ID of 107298
Processing row with Object ID of 107299
Processing row with Object ID of 107300
Processing row with Object ID of 107301
Processing row with Object ID of 107302
Processing row with Object ID of 107303
Processing row with Object ID of 107304
Processing row with Object ID of 107305
Processing row with Object ID of 107306
Processing row with Object ID of 107307
Processing row with Object ID of 107308
Processing row with Object ID of 107309
Processing row with Object ID of 107310
Processing row with Object ID of 107311
Processing row with Object ID of 107312
Processing row with Object ID of 107313
Processing row with Object ID of 107314
Processing row with Object ID of 107315
Processing row with Object ID of 107316
Processing row with Object ID of 107317
Processing row with Object ID of 107318
Processing row with Object ID of 107319


Processing row with Object ID of 107961
Processing row with Object ID of 107962
Processing row with Object ID of 107963
Processing row with Object ID of 107964
Processing row with Object ID of 107965
Processing row with Object ID of 107966
Processing row with Object ID of 107967
Processing row with Object ID of 107968
Processing row with Object ID of 107969
Processing row with Object ID of 107970
Processing row with Object ID of 107971
Processing row with Object ID of 107972
Processing row with Object ID of 107973
Processing row with Object ID of 107974
Processing row with Object ID of 107975
Processing row with Object ID of 107976
Processing row with Object ID of 107977
Processing row with Object ID of 107978
Processing row with Object ID of 107979
Processing row with Object ID of 107980
Processing row with Object ID of 107981
Processing row with Object ID of 107982
Processing row with Object ID of 107983
Processing row with Object ID of 107984
Processing row with Object ID of 107985


Processing row with Object ID of 108474
Processing row with Object ID of 108475
Processing row with Object ID of 108476
Processing row with Object ID of 108477
Processing row with Object ID of 108478
Processing row with Object ID of 108479
Processing row with Object ID of 108480
Processing row with Object ID of 108481
Processing row with Object ID of 108482
Processing row with Object ID of 108483
Processing row with Object ID of 108484
Processing row with Object ID of 108485
Processing row with Object ID of 108486
Processing row with Object ID of 108487
Processing row with Object ID of 108488
Processing row with Object ID of 108489
Processing row with Object ID of 108490
Processing row with Object ID of 108491
Processing row with Object ID of 108492
Processing row with Object ID of 108493
Processing row with Object ID of 108494
Processing row with Object ID of 108495
Processing row with Object ID of 108496
Processing row with Object ID of 108497
Processing row with Object ID of 108498


Processing row with Object ID of 108993
Processing row with Object ID of 108994
Processing row with Object ID of 108995
Processing row with Object ID of 108996
Processing row with Object ID of 108997
Processing row with Object ID of 108998
Processing row with Object ID of 108999
Processing row with Object ID of 109000
Processing row with Object ID of 109001
Processing row with Object ID of 109002
Processing row with Object ID of 109003
Processing row with Object ID of 109004
Processing row with Object ID of 109005
Processing row with Object ID of 109006
Processing row with Object ID of 109007
Processing row with Object ID of 109008
Processing row with Object ID of 109009
Processing row with Object ID of 109010
Processing row with Object ID of 109011
Processing row with Object ID of 109012
Processing row with Object ID of 109013
Processing row with Object ID of 109014
Processing row with Object ID of 109015
Processing row with Object ID of 109016
Processing row with Object ID of 109017


In [100]:
# # Get fields in the excel
# fields = [field.name for field in arcpy.ListFields(fgdb_table)]

# # Start iterating on the target Polygonal FC with an insert cursor
# with arcpy.da.InsertCursor(poly_fc, ["SHAPE@"]) as insertcursor:
    
#     # Start iterating on the input file geodatabase table with a searchcursor
#     with arcpy.da.SearchCursor(fgdb_table, fields) as searchcursor:
#         for row in searchcursor:
#             objectid = row[0]
#             waid = row[1]
#             country_caption = row[2]
#             area_caption = row[3]
#             emma_id = row[4]
#             polygon = row[5]
#             walevel = row[6]
#             awtcaption = row[7]
#             watype = row[8]
#             wafrom = row[9]
#             wato = row[10]
#             watext = row[11]
#             print("Processing row with Object ID of {0}".format(str(objectid)))
            
#             try:
#                 polygon_objects_list = prepare_polygon_object(polygon)
#                 insertcursor.insertRow(polygon_objects_list)
#             except ValueError:
#                 print("Could not read geometry from input list. Bypassing...")

Processing row with Object ID of 1
Processing row with Object ID of 2
Processing row with Object ID of 3
Processing row with Object ID of 4
Processing row with Object ID of 5
Processing row with Object ID of 6
Processing row with Object ID of 7
Processing row with Object ID of 8
Processing row with Object ID of 9
Processing row with Object ID of 10
Processing row with Object ID of 11
Processing row with Object ID of 12
Processing row with Object ID of 13
Processing row with Object ID of 14
Processing row with Object ID of 15
Processing row with Object ID of 16
Processing row with Object ID of 17
Processing row with Object ID of 18
Processing row with Object ID of 19
Processing row with Object ID of 20
Processing row with Object ID of 21
Processing row with Object ID of 22
Processing row with Object ID of 23
Processing row with Object ID of 24
Processing row with Object ID of 25
Processing row with Object ID of 26
Processing row with Object ID of 27
Processing row with Object ID of 28
P

Processing row with Object ID of 242
Processing row with Object ID of 243
Processing row with Object ID of 244
Processing row with Object ID of 245
Processing row with Object ID of 246
Processing row with Object ID of 247
Processing row with Object ID of 248
Processing row with Object ID of 249
Processing row with Object ID of 250
Processing row with Object ID of 251
Processing row with Object ID of 252
Processing row with Object ID of 253
Processing row with Object ID of 254
Processing row with Object ID of 255
Processing row with Object ID of 256
Processing row with Object ID of 257
Processing row with Object ID of 258
Processing row with Object ID of 259
Processing row with Object ID of 260
Processing row with Object ID of 261
Processing row with Object ID of 262
Processing row with Object ID of 263
Processing row with Object ID of 264
Processing row with Object ID of 265
Processing row with Object ID of 266
Processing row with Object ID of 267
Processing row with Object ID of 268
P

Processing row with Object ID of 671
Processing row with Object ID of 672
Processing row with Object ID of 673
Processing row with Object ID of 674
Processing row with Object ID of 675
Processing row with Object ID of 676
Processing row with Object ID of 677
Processing row with Object ID of 678
Processing row with Object ID of 679
Processing row with Object ID of 680
Processing row with Object ID of 681
Processing row with Object ID of 682
Processing row with Object ID of 683
Processing row with Object ID of 684
Processing row with Object ID of 685
Processing row with Object ID of 686
Processing row with Object ID of 687
Processing row with Object ID of 688
Processing row with Object ID of 689
Processing row with Object ID of 690
Processing row with Object ID of 691
Processing row with Object ID of 692
Processing row with Object ID of 693
Processing row with Object ID of 694
Processing row with Object ID of 695
Processing row with Object ID of 696
Processing row with Object ID of 697
P

Processing row with Object ID of 1297
Processing row with Object ID of 1298
Processing row with Object ID of 1299
Processing row with Object ID of 1300
Processing row with Object ID of 1301
Processing row with Object ID of 1302
Processing row with Object ID of 1303
Processing row with Object ID of 1304
Processing row with Object ID of 1305
Processing row with Object ID of 1306
Processing row with Object ID of 1307
Processing row with Object ID of 1308
Processing row with Object ID of 1309
Processing row with Object ID of 1310
Processing row with Object ID of 1311
Processing row with Object ID of 1312
Processing row with Object ID of 1313
Processing row with Object ID of 1314
Processing row with Object ID of 1315
Processing row with Object ID of 1316
Processing row with Object ID of 1317
Processing row with Object ID of 1318
Processing row with Object ID of 1319
Processing row with Object ID of 1320
Processing row with Object ID of 1321
Processing row with Object ID of 1322
Processing r

Processing row with Object ID of 1875
Processing row with Object ID of 1876
Processing row with Object ID of 1877
Processing row with Object ID of 1878
Processing row with Object ID of 1879
Processing row with Object ID of 1880
Processing row with Object ID of 1881
Processing row with Object ID of 1882
Processing row with Object ID of 1883
Processing row with Object ID of 1884
Processing row with Object ID of 1885
Processing row with Object ID of 1886
Processing row with Object ID of 1887
Processing row with Object ID of 1888
Processing row with Object ID of 1889
Processing row with Object ID of 1890
Processing row with Object ID of 1891
Processing row with Object ID of 1892
Processing row with Object ID of 1893
Processing row with Object ID of 1894
Processing row with Object ID of 1895
Processing row with Object ID of 1896
Processing row with Object ID of 1897
Processing row with Object ID of 1898
Processing row with Object ID of 1899
Processing row with Object ID of 1900
Processing r

Processing row with Object ID of 2565
Processing row with Object ID of 2566
Processing row with Object ID of 2567
Processing row with Object ID of 2568
Processing row with Object ID of 2569
Processing row with Object ID of 2570
Processing row with Object ID of 2571
Processing row with Object ID of 2572
Processing row with Object ID of 2573
Processing row with Object ID of 2574
Processing row with Object ID of 2575
Processing row with Object ID of 2576
Processing row with Object ID of 2577
Processing row with Object ID of 2578
Processing row with Object ID of 2579
Processing row with Object ID of 2580
Processing row with Object ID of 2581
Processing row with Object ID of 2582
Processing row with Object ID of 2583
Processing row with Object ID of 2584
Processing row with Object ID of 2585
Processing row with Object ID of 2586
Processing row with Object ID of 2587
Processing row with Object ID of 2588
Processing row with Object ID of 2589
Processing row with Object ID of 2590
Processing r

Processing row with Object ID of 3104
Processing row with Object ID of 3105
Processing row with Object ID of 3106
Processing row with Object ID of 3107
Processing row with Object ID of 3108
Processing row with Object ID of 3109
Processing row with Object ID of 3110
Processing row with Object ID of 3111
Processing row with Object ID of 3112
Processing row with Object ID of 3113
Processing row with Object ID of 3114
Processing row with Object ID of 3115
Processing row with Object ID of 3116
Processing row with Object ID of 3117
Processing row with Object ID of 3118
Processing row with Object ID of 3119
Processing row with Object ID of 3120
Processing row with Object ID of 3121
Processing row with Object ID of 3122
Processing row with Object ID of 3123
Processing row with Object ID of 3124
Processing row with Object ID of 3125
Processing row with Object ID of 3126
Processing row with Object ID of 3127
Processing row with Object ID of 3128
Processing row with Object ID of 3129
Processing r

Processing row with Object ID of 3650
Processing row with Object ID of 3651
Processing row with Object ID of 3652
Processing row with Object ID of 3653
Processing row with Object ID of 3654
Processing row with Object ID of 3655
Processing row with Object ID of 3656
Processing row with Object ID of 3657
Processing row with Object ID of 3658
Processing row with Object ID of 3659
Processing row with Object ID of 3660
Processing row with Object ID of 3661
Processing row with Object ID of 3662
Processing row with Object ID of 3663
Processing row with Object ID of 3664
Processing row with Object ID of 3665
Processing row with Object ID of 3666
Processing row with Object ID of 3667
Processing row with Object ID of 3668
Processing row with Object ID of 3669
Processing row with Object ID of 3670
Processing row with Object ID of 3671
Processing row with Object ID of 3672
Processing row with Object ID of 3673
Processing row with Object ID of 3674
Processing row with Object ID of 3675
Processing r

Processing row with Object ID of 4203
Processing row with Object ID of 4204
Processing row with Object ID of 4205
Processing row with Object ID of 4206
Processing row with Object ID of 4207
Processing row with Object ID of 4208
Processing row with Object ID of 4209
Processing row with Object ID of 4210
Processing row with Object ID of 4211
Processing row with Object ID of 4212
Processing row with Object ID of 4213
Processing row with Object ID of 4214
Processing row with Object ID of 4215
Processing row with Object ID of 4216
Processing row with Object ID of 4217
Processing row with Object ID of 4218
Processing row with Object ID of 4219
Processing row with Object ID of 4220
Processing row with Object ID of 4221
Processing row with Object ID of 4222
Processing row with Object ID of 4223
Processing row with Object ID of 4224
Processing row with Object ID of 4225
Processing row with Object ID of 4226
Processing row with Object ID of 4227
Processing row with Object ID of 4228
Processing r

KeyboardInterrupt: 